# Stored procedure `pivot()` explanation
#### The how and why of creating a new simple pivoted table from a given base table.

In [1]:
import pandas as pd
from data201 import db_connection, df_query

In [2]:
conn = db_connection(config_file = 'pivot_test.ini')
cursor = conn.cursor()

In [3]:
pd.set_option('display.max_colwidth', 1000)

### Stored procedure parameters:
- #### `database_name`: the name of the database containing the table to pivot
- #### `base_table_name`: the name of the table to pivot
- #### `base_primary_key_name`: the name of the primary key column of the base table
- #### `pivot_primary_key_name`: the desired name of the primary key column of the pivoted table

#### The name of the created pivot table will be the base table name with `_pivoted` appended.  
```
CREATE PROCEDURE pivot(
	IN database_name VARCHAR(32),
    IN base_table_name VARCHAR(32),
    IN base_primary_key_name VARCHAR(32),
    IN pivoted_primary_key_name VARCHAR(32)
)
```
#### In the following excerpts, user-defined variables `@database_name`, `@base_table_name`,  `@base_primary_key_name`, and `pivoted_primary_key_name` take the place of the stored procedure's parameters. We'll test with database `pivot_test` and its table `fruits` with primary key `store_id`.

In [4]:
cursor.execute("SET @database_name = 'pivot_test'")
cursor.execute("SET @base_table_name = 'fruits'")
cursor.execute("SET @base_primary_key_name = 'store_id'")
cursor.execute("SET @pivoted_primary_key_name = 'fruit_id'")

df_query(conn,
   """
   SELECT @database_name, @base_table_name, 
          @base_primary_key_name, @pivoted_primary_key_name
   """
)

@database_name @base_table_name @base_primary_key_name  \
0     pivot_test           fruits               store_id   

  @pivoted_primary_key_name  
0                  fruit_id

### Table `fruits` to pivot.

In [5]:
df_query(conn, 'SELECT * FROM fruits')

store_id  apples  oranges  bananas  peaches  pears
0  store_1     101      102      103      104    105
1  store_2     201      202      203      204    205
2  store_3     301      302      303      304    305

### Call stored procedure `pivot()` to pivot the table.

In [6]:
#            database_name: pivot_test
#          base table_name: fruits
#    base_primary_key_name: store_id
# pivoted_primary_key_name: fruit_id

cursor.execute("CALL pivot('pivot_test', 'fruits', 'store_id', 'fruit_id')")

### The resulting pivoted table `fruits_pivoted`.

In [7]:
df_query(conn, 'SELECT * FROM fruits_pivoted')

fruit_id  store_1  store_2  store_3
0   apples      101      201      301
1  bananas      103      203      303
2  oranges      102      202      302
3  peaches      104      204      304
4    pears      105      205      305

# How to pivot an database table.
### Restrictions:
- #### The base table's primary key must be its first column, and the key's values must be varchar (string).
- #### Since rows become columns and columns become rows after pivoting, all the data in the base table other than the primary key's values must be from the same domain (i.e., they all must have the same datatype).
- #### Since the base table's primary key values will become the names of the pivoted table's columns, each value must be a legitimate column name.

### Base table's primary key values
#### The built-in `GROUP_CONCAT` function constructs a comma-separated list of the base table's primary key values. This will be useful later for inserting values into the pivoted table.

In [8]:
cursor.execute(
    """
    SELECT GROUP_CONCAT(store_id)
    INTO @pivoted_col_names
    FROM fruits
    """
)

df_query(conn, 'SELECT @pivoted_col_names')

@pivoted_col_names
0  store_1,store_2,store_3

### Prepared statements
#### We want the stored procedure to work with any base table. Therefore, we need to replace `store_id` with the value of parameter `base_primary_key_name` and `fruits` with the value of parameter `base_table_name`. We can create the SQL command as a string using the built-in `CONCAT()` function. (In this excerpt, the user-defined variables `@base_primary_key_name` and `@base_table_name` take the place of the stored procedure's parameters.)

In [9]:
cursor.execute(
    """
    SET @sql_string = CONCAT(
        'SELECT GROUP_CONCAT(', @base_primary_key_name, ') ',
        'INTO @pivoted_col_names FROM ', @base_table_name
    );
    """
)

df_query(conn, 'SELECT @sql_string')

@sql_string
0  SELECT GROUP_CONCAT(store_id) INTO @pivoted_col_names FROM fruits

#### Once we have a SQL string, we can create a prepared statement from it, and then execute the statement.

In [10]:
cursor.execute('PREPARE sql_stmt FROM @sql_string')

df_query(conn, 'SELECT @pivoted_col_names')

@pivoted_col_names
0  store_1,store_2,store_3

#### Afterward, we should deallocate the prepared statement.

In [11]:
cursor.execute('DEALLOCATE PREPARE sql_stmt')

#### Helper stored procedure `exec_stmt()` does all this. We simply pass it the SQL string. (In this excerpt, the user-defined variables `@base_primary_key_name` and `@base_table_name` take the place of the stored procedure's parameters.)

In [12]:
cursor.execute("SET @pivoted_col_names = ''")

cursor.execute(
    """
    CALL exec_stmt(CONCAT(
        'SELECT GROUP_CONCAT(', @base_primary_key_name, ') ',
        ' INTO @pivoted_col_names FROM ', @base_table_name
    ));
    """
)

df_query(conn, 'SELECT @pivoted_col_names')

@pivoted_col_names
0  store_1,store_2,store_3

#### Prepend the pivoted column names with the name of the pivoted primary key name.  (In this excerpt, the user-defined variables @pivoted_primary_key_name takes the place of the stored procedure's parameters.)

In [13]:
cursor.execute(
    """
    SET @pivoted_col_names = CONCAT(@pivoted_primary_key_name, 
                                    ', ', @pivoted_col_names);
    """
)

df_query(conn, 'SELECT @pivoted_col_names')

@pivoted_col_names
0  fruit_id, store_1,store_2,store_3

### Create the pivoted table
#### To create the table `fruits_pivoted`:
```
CREATE TABLE fruits_pivoted
(
    fruit_id VARCHAR(32) NOT NULL,
    store_1 INT,
    store_2 INT,
    store_3 INT,
    PRIMARY KEY (fruit_id)
)
```
#### For the `fruits_pivoted` example:

In [14]:
cursor.execute('SET @key = @base_primary_key_name')

cursor.execute(
    """
    CALL exec_stmt(CONCAT(
        "SELECT GROUP_CONCAT(", @key, ", ' INT') ",
        "INTO @field_list ",
        "FROM ", @base_table_name
    ))
    """
)

df_query(conn, 'SELECT @field_list')

@field_list
0  store_1 INT,store_2 INT,store_3 INT

#### The SQL string to create the pivoted table. The name of the pivoted table's primary key column is determined by the caller of the stored procedure as the value of the parameter `pivoted_primary_key_name`. (In this excerpt, the user-defined variables `@base_table_name`, `@pivoted_table_name`, and `@pivoted_primary_key_name` take the place of the stored procedure's parameters.)

In [15]:
cursor.execute(
    """
    SET @pivoted_table_name = CONCAT(@base_table_name, '_pivoted')
    """
)

cursor.execute(
    """
    SET @create_string = CONCAT(
        'CREATE TABLE ', @pivoted_table_name,
        '(', @pivoted_primary_key_name, ' VARCHAR(32) NOT NULL, ', 
        @field_list,
        ', PRIMARY KEY (', @pivoted_primary_key_name, ') ',
        ')'
    )
    """
)

df_query(conn, 'SELECT @create_string')

@create_string
0  CREATE TABLE fruits_pivoted(fruit_id VARCHAR(32) NOT NULL, store_1 INT,store_2 INT,store_3 INT, PRIMARY KEY (fruit_id) )

#### Therefore, to create any pivoted table. (In this excerpt, the user-defined variables `@base_table_name`, `@pivoted_table_name`, and `@pivoted_primary_key_name` take the place of the stored procedure's parameters.)

In [16]:
cursor.execute(
    """
    CALL exec_stmt(CONCAT(
        'DROP TABLE IF EXISTS ', @pivoted_table_name
    ));
    """
)

cursor.execute(
    """
    CALL exec_stmt(CONCAT(
        'CREATE TABLE ', @pivoted_table_name,
        '(', @pivoted_primary_key_name, ' VARCHAR(32) NOT NULL, ', 
        @field_list,
        ', PRIMARY KEY (', @pivoted_primary_key_name, ') ',
        ')'
    ))
    """
)


### Columns of the base table
#### To create table `fruits_pivoted`, we need to go column by column, left to right, from the base table `fruits` and insert the base column values row by row into the pivoted table `fruits_pivoted`. The column names of the base table become the primary key values of the pivoted table, and the primary key values of the base table become the column names of the pivoted table. 
#### We want the stored procedure to work with any base table. Therefore, we must query the built-in table `information_schema.columns`. (In this excerpt, the user-defined variables `@database_name` and `@base_table_name` take the place of the stored procedure's parameters.)

In [17]:
df_query(conn,
    """
    SELECT *
    FROM information_schema.columns
    WHERE table_schema = @database_name
      AND table_name   = @base_table_name
    ORDER BY ordinal_position;
    """
)

TABLE_CATALOG TABLE_SCHEMA TABLE_NAME COLUMN_NAME  ORDINAL_POSITION  \
0           def   pivot_test     fruits    store_id                 1   
1           def   pivot_test     fruits      apples                 2   
2           def   pivot_test     fruits     oranges                 3   
3           def   pivot_test     fruits     bananas                 4   
4           def   pivot_test     fruits     peaches                 5   
5           def   pivot_test     fruits       pears                 6   

  COLUMN_DEFAULT IS_NULLABLE DATA_TYPE  CHARACTER_MAXIMUM_LENGTH  \
0           None          NO   varchar                       8.0   
1           None         YES       int                       NaN   
2           None         YES       int                       NaN   
3           None         YES       int                       NaN   
4           None         YES       int                       NaN   
5           None         YES       int                       NaN   

   CHARACTER_OCTET_LENGTH  ...  DATETIME_PRECISION  CHARACTER_SET_NAME  \
0                    32.0  ...                None             utf8mb4   
1                     NaN  ...                None                None   
2                     NaN  ...                None                None   
3                     NaN  ...                None                None   
4                     NaN  ...                None                None   
5                     NaN  ...                None                None   

       COLLATION_NAME COLUMN_TYPE COLUMN_KEY EXTRA  \
0  utf8mb4_0900_ai_ci  varchar(8)        PRI         
1                None         int                    
2                None         int                    
3                None         int                    
4                None         int                    
5                None         int                    

                        PRIVILEGES COLUMN_COMMENT GENERATION_EXPRESSION SRS_ID  
0  select,insert,update,references                                        None  
1  select,insert,update,references                                        None  
2  select,insert,update,references                                        None  
3  select,insert,update,references                                        None  
4  select,insert,update,references                                        None  
5  select,insert,update,references                                        None  

[6 rows x 22 columns]

#### We only want the column names of the base table, not including the primary key column.

In [18]:
df_query(conn,
    """
    SELECT column_name
    FROM information_schema.columns
    WHERE table_schema = @database_name
      AND table_name   = @base_table_name
      AND ordinal_position > 1
    ORDER BY ordinal_position;
    """
)

COLUMN_NAME
0      apples
1     oranges
2     bananas
3     peaches
4       pears

### `CURSOR` and `CONTINUE HANDLER` for the base table columns
#### In order to process the base table column by column, we don't want the column names all at once. Instead, we want the names one at a time. To do this, we defined a cursor:
```
DECLARE base_col_cursor CURSOR FOR
    SELECT column_name
    FROM information_schema.columns
    WHERE table_schema = database_name
      AND table_name   = base_table_name
      AND ordinal_position > 1
    ORDER BY ordinal_position;
```
#### To open the cursor:
```
OPEN base_col_cursor;
```
#### Then, to get the next column name each time into the stored procedure's local variable `base_col_name`:
```
FETCH base_col_cursor INTO base_col_name;
```
#### We also define a continue handler that's automatically called when the cursor has no more values:
```
DECLARE CONTINUE HANDLER FOR NOT FOUND
    SET no_more_columns = TRUE;
```
Local variable `no_more_columns` is initialized to `FALSE`:
```
    DECLARE no_more_columns BOOL DEFAULT FALSE;
```
#### A `WHILE` loop iterates over the column names, one at a time:
```
FETCH base_col_cursor INTO base_col_name;

WHILE NOT no_more_columns DO
    ...

    FETCH base_col_cursor INTO base_col_name;
END WHILE; 
```

### Values from one base table column
#### `GROUP_CONCAT()` constructs a comma-separated list of values from one base table column. For example, column `apples` from table `fruits` produces values for the first row of table `fruits_pivoted`.

In [19]:
cursor.execute(
    """
    SELECT GROUP_CONCAT(apples)
    INTO @pivoted_values
    FROM fruits
    """
)

df_query(conn, 'SELECT @pivoted_values')

@pivoted_values
0     101,201,301

#### Prepend the base column column name, and we have all the values for the pivoted table's first row.

In [20]:
cursor.execute(
    """
    SET @pivoted_values = CONCAT('apple', ', ', @pivoted_values)
    """
)

df_query(conn, 'SELECT @pivoted_values')

@pivoted_values
0  apple, 101,201,301

### Inside the `WHILE` loop
#### Thne `WHILE` loop iterates over all of any base table's columns. We can get the comma-separated values from each base column, one column at a time, since the `base_col_cursor` supplies the base column names.
```
CALL exec_stmt(CONCAT(
    'SELECT GROUP_CONCAT(', base_col_name, ') ',
    'INTO @pivoted_values ',
    'FROM ', base_table_name
))
```

#### Prepend the base column name as the pivoted row's primary key value:
```
SET @pivoted_values = CONCAT("'", base_col_name, 
                             "', ", @pivoted_values);
```
#### And insert the row into the pivoted table:
```
CALL exec_stmt(CONCAT(
    'INSERT INTO ', pivoted_table_name,
    '(', @pivoted_col_names, ') ',
    'VALUES (', @pivoted_values, ')'
));
```

In [21]:
cursor.close()
conn.close()